<a href="https://colab.research.google.com/github/gtyellow/NlpYoutubeTranslatorOriginal/blob/main/Youtubetranslate2.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
#This code is optimized for a google colab environment.

#It downloads a clip from youtube in most languages and translates into english

In [1]:
!pip install pydub
!pip install IPython
!pip install yt_dlp
!pip install ffmpeg

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 34.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 172.1/172.1 kB 11.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.2/3.2 MB 71.4 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for ffmpeg: filename=ffmpeg-1.4-py3-none-any.whl size=6082 sha256=4a749b52096a5483fd0bf0a44d2b78a1d34b45941bda1ba368bc6df6a980420c
  Stored in directory: /root/.cache/pip/wheels/8e/7a/69/cd6aeb83b126a7f04cbe7c9d929028dc52a6e7d525ff56003a
Successfully built ffmpeg


In [2]:
#Step 1 Download Libraries

import torchaudio
import torch
from pydub import AudioSegment
from IPython.display import Audio
from yt_dlp import YoutubeDL
import ffmpeg
import time
import io

from transformers import AutoProcessor, SeamlessM4Tv2Model

import sentencepiece
#print(f"sentencepiece version: {sentencepiece.__version__}")

In [3]:
tick=time.time()
####
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

processor = AutoProcessor.from_pretrained("facebook/seamless-m4t-v2-large")
model = SeamlessM4Tv2Model.from_pretrained(
    "facebook/seamless-m4t-v2-large",
    torch_dtype="float16"  # Use mixed precision for faster loading and inference
).to(device)
#####model = SeamlessM4Tv2Model.from_pretrained("facebook/seamless-m4t-v2-large")

tock=time.time()
print("Model Load time: ", str(round(tock-tick, 3)), " seconds.")

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


preprocessor_config.json:   0%|          | 0.00/1.78k [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/19.7k [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/5.17M [00:00<?, ?B/s]

added_tokens.json:   0%|          | 0.00/2.07k [00:00<?, ?B/s]

...

model-00001-of-00002.safetensors:   0%|          | 0.00/5.00G [00:00<?, ?B/s]

model-00002-of-00002.safetensors:   0%|          | 0.00/4.24G [00:00<?, ?B/s]

Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

generation_config.json:   0%|          | 0.00/9.91M [00:00<?, ?B/s]

Model Load time:  305.236  seconds.


In [4]:
tick=time.time()
# Download YouTube clip and convert to suitable format
url = "https://www.youtube.com/watch?v=PI8KiEx_ZQM"
ydl_opts = {
    'format': 'bestaudio/best',
    'outtmpl': 'temp_audio.%(ext)s',
    'postprocessors': [{
        'key': 'FFmpegExtractAudio',
        'preferredcodec': 'wav',
        'preferredquality': '192',
    }],
}

with YoutubeDL(ydl_opts) as ydl:
    ydl.download([url])

tock=time.time()
print("Download time: ", str(round(tock-tick, 2)), " seconds")

[youtube] Extracting URL: https://www.youtube.com/watch?v=PI8KiEx_ZQM
[youtube] PI8KiEx_ZQM: Downloading webpage
[youtube] PI8KiEx_ZQM: Downloading ios player API JSON
[youtube] PI8KiEx_ZQM: Downloading mweb player API JSON
[youtube] PI8KiEx_ZQM: Downloading player 5b77d519
[youtube] PI8KiEx_ZQM: Downloading m3u8 information
[info] PI8KiEx_ZQM: Downloading 1 format(s): 251
[download] Destination: temp_audio.webm
[download] 100% of    2.24MiB in 00:00:00 at 4.84MiB/s   
[ExtractAudio] Destination: temp_audio.wav
Deleting original file temp_audio.webm (pass -k to keep)
Download time:  3.75  seconds


In [5]:
# Load the downloaded WAV file into tensor and resample
tick = time.time()

# Load and trim the audio using torchaudio
waveform, sample_rate = torchaudio.load("temp_audio.wav")
start_time = 34  # Start time in seconds
end_time = 50  # End time in seconds

# Trim the audio
start_sample = int(start_time * sample_rate)
end_sample = int(end_time * sample_rate)
waveform = waveform[:, start_sample:end_sample]

# Resample to 16 kHz if necessary
target_sample_rate = 16000
if sample_rate != target_sample_rate:
    resampler = torchaudio.transforms.Resample(sample_rate, target_sample_rate)
    waveform = resampler(waveform)

# Normalize the waveform
waveform = waveform / waveform.abs().max()

# Ensure single-channel audio (if necessary)
if waveform.size(0) > 1:
    waveform = waveform.mean(dim=0, keepdim=True)

# Add batch dimension
waveform = waveform.unsqueeze(0).to(device)  # Move to GPU

# Process the waveform using the processor
inputs = processor(
    audios=waveform.squeeze().cpu().numpy(),  # Move to CPU and convert to NumPy
    sampling_rate=target_sample_rate,
    return_tensors="pt"
)

inputs = {key: value.to(device) for key, value in inputs.items()}  # Move to GPU


tock = time.time()
print("Load time: ", str(round(tock - tick, 2)), " seconds")

Load time:  0.48  seconds


In [6]:

# Step 5: (optional) Play the trimmed audio.  Useful for testing to make sure download and trimming works


audio = AudioSegment.from_wav("temp_audio.wav")
trimmed_audio = audio[34000:50000]  # Trim from 2 seconds to 22 seconds

# Convert trimmed audio to bytes
audio_bytes = io.BytesIO()
trimmed_audio.export(audio_bytes, format="wav")
audio_bytes.seek(0)  # Reset the buffer position

# Play the audio
audio_to_play = Audio(audio_bytes.read(), rate=trimmed_audio.frame_rate)
display(audio_to_play)


In [7]:
# Translate the clip

tick = time.time()
translated_audio = model.generate(**inputs, tgt_lang="eng")[0]
translated_audio = translated_audio.cpu().numpy().squeeze()  # Move to CPU for playback
tock = time.time()
print("Translate time: ", str(round(tock - tick, 2)), " seconds")

Translate time:  4.94  seconds


In [8]:
#Play the clip
tick=time.time()

sample_rate = model.config.sampling_rate
tock=time.time()
print("Play time: ", str(round(tock-tick, 3)), " seconds")

#Audio(audio_array_from_audio, rate=sample_rate)
Audio(translated_audio, rate=sample_rate)


Play time:  0.0  seconds


In [9]:

# Step 5: (optional) Play the trimmed audio.  Useful for testing to make sure download and trimming works



# Export the trimmed audio to a new WAV file
trimmed_audio.export("trimmed_audio.wav", format="wav")

audio_to_play = Audio(filename="trimmed_audio.wav")
display(audio_to_play)
